# Exploratory Data Analysis (EDA)

In [2]:
require 'open-uri'
require 'json'
require 'daru'
require 'distribution'
require 'sqlite3'
require './cluster'
require'./regression'
include Regression
require './data_analysis'
include DataAnalysis

"if(window['d3'] === undefined ||\n   window['Nyaplot'] === undefined){\n    var path = {\"d3\":\"https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min\",\"downloadable\":\"http://cdn.rawgit.com/domitry/d3-downloadable/master/d3-downloadable\"};\n\n\n\n    var shim = {\"d3\":{\"exports\":\"d3\"},\"downloadable\":{\"exports\":\"downloadable\"}};\n\n    require.config({paths: path, shim:shim});\n\n\nrequire(['d3'], function(d3){window['d3']=d3;console.log('finished loading d3');require(['downloadable'], function(downloadable){window['downloadable']=downloadable;console.log('finished loading downloadable');\n\n\tvar script = d3.select(\"head\")\n\t    .append(\"script\")\n\t    .attr(\"src\", \"http://cdn.rawgit.com/domitry/Nyaplotjs/master/release/nyaplot.js\")\n\t    .attr(\"async\", true);\n\n\tscript[0][0].onload = script[0][0].onreadystatechange = function(){\n\n\n\t    var event = document.createEvent(\"HTMLEvents\");\n\t    event.initEvent(\"load_nyaplot\",false,false);\n\t    win

[5.276292762964063, 1.3233006338355773, 0.030004205647377657, 0.04574682751265766, 0.015266880111503059, 0.01842005320894797, 0.028095891662442574, 0.018256662334378712, 0.013239762473924548, 0.016153760449136006, 0.004621531806650666, 0.002296942590629463, 0.003069426390117339]


Object

In [3]:
dir = "#{ENV['HOME']}/cs6140/final_project"
db = SQLite3::Database.new "#{dir}/credit_risk_data.db"
db.results_as_hash = true

true

In [4]:
column_types = Hash.new
db.execute("PRAGMA table_info(application_train);").each do |row|
  column_types[row["name"]] = row["type"]
end
1

1

##  Data is balanced or imbalanced
![Frequency](target.png)
#### *Data is imbalanced as there are only 8% of data for Target == 1*

In [6]:
table = get_info_gain db,"application_train"
table = table.sort_by do |item|
   -item[1]
end 
#puts table
column1 = table.collect {|x| x[0]}
column2 = table.collect {|x| x[1]}
column3 = table.collect {|x| x[3]}

df = Daru::DataFrame.new({"Feature Name" => column1, "Information Gain" => column2 , "Frequency" => column3})

Interrupt: 

##  Information Gain and Frequency of Features in Application Train
#### *Top 25 Features are-*
![DA](infog.png)

In [21]:
sql = <<SQL
create temp table bureau_temp
as select * from bureau as a join 
(select application_train.SK_ID_CURR, application_train.TARGET from application_train) b
on a.SK_ID_CURR == b.SK_ID_CURR
limit 10000
SQL

begin
db.execute(sql) 
rescue 
db.execute("drop table bureau_temp")
db.execute(sql)
end


table = get_info_gain db,"bureau_temp"
table = table.sort_by do |item|
   -item[1].to_f
end 
#puts table
column1 = table.collect {|x| x[0]}
column2 = table.collect {|x| x[1]}
column3 = table.collect {|x| x[3]}

df = Daru::DataFrame.new({"Feature Name" => column1, "Information Gain" => column2 , "Frequency" => column3})

#<Daru::DataFrame(18x3)>
            Feature Na Informatio  Frequency
          0     TARGET 0.37958203        1.0
          1 DAYS_ENDDA 0.00442595     0.6215
          2 DAYS_CREDI 0.00412976        1.0
          3 CREDIT_ACT 0.00330612          0
          4 CREDIT_TYP 0.00302606          0
          5 SK_ID_CURR 0.00110929        1.0
          6 AMT_CREDIT 0.00066600        1.0
          7 SK_ID_BURE 0.00058363        1.0
          8 DAYS_CREDI 0.00056136     0.9365
          9 AMT_CREDIT 0.00037630     0.6685
         10 AMT_CREDIT 0.00037630     0.3796
         11 AMT_CREDIT 0.00023219     0.8474
         12 AMT_CREDIT 0.00018792        1.0
         13 AMT_ANNUIT 0.00017686     0.1836
         14 DAYS_CREDI 0.00011050        1.0
        ...        ...        ...        ...

##  Information Gain and Frequency of Features in Bureau
#### *All Features are-*
![DA](bur.png)

In [22]:
sql = <<SQL
create temp table POS_CASH_balance_temp
as select * from POS_CASH_balance as a join 
(select application_train.SK_ID_CURR, application_train.TARGET from application_train) b
on a.SK_ID_CURR == b.SK_ID_CURR
limit 10000
SQL

begin
db.execute(sql) 
rescue 
db.execute("drop table POS_CASH_balance_temp")
db.execute(sql)
end


table = get_info_gain db,"POS_CASH_balance_temp"
table = table.sort_by do |item|
   -item[1].to_f
end 
#puts table
column1 = table.collect {|x| x[0]}
column2 = table.collect {|x| x[1]}
column3 = table.collect {|x| x[3]}

df = Daru::DataFrame.new({"Feature Name" => column1, "Information Gain" => column2 , "Frequency" => column3})

#<Daru::DataFrame(9x3)>
            Feature Na Informatio  Frequency
          0     TARGET 0.39402269        1.0
          1 SK_ID_PREV 0.00050168        1.0
          2 NAME_CONTR 0.00032658          0
          3 SK_ID_CURR 0.00022444        1.0
          4 SK_DPD_DEF 0.00018033        1.0
          5 CNT_INSTAL 0.00017143     0.9985
          6 MONTHS_BAL 0.00014603        1.0
          7 CNT_INSTAL 7.70064318     0.9985
          8     SK_DPD 7.00370847        1.0

##  Information Gain and Frequency of Features in POS_CASH_balance
#### *All Features are-*
![DA](posh.png)

In [23]:
sql = <<SQL
create temp table previous_application_temp
as select * from previous_application as a join 
(select application_train.SK_ID_CURR, application_train.TARGET from application_train) b
on a.SK_ID_CURR == b.SK_ID_CURR
limit 10000
SQL

begin
db.execute(sql) 
rescue 
db.execute("drop table previous_application_temp")
db.execute(sql)
end


table = get_info_gain db,"previous_application_temp"
table = table.sort_by do |item|
   -item[1].to_f
end 
#puts table
column1 = table.collect {|x| x[0]}
column2 = table.collect {|x| x[1]}
column3 = table.collect {|x| x[3]}

df = Daru::DataFrame.new({"Feature Name" => column1, "Information Gain" => column2 , "Frequency" => column3})

#<Daru::DataFrame(38x3)>
            Feature Na Informatio  Frequency
          0     TARGET 0.41196912        1.0
          1 SELLERPLAC 0.03784594          0
          2 PRODUCT_CO 0.00367586          0
          3 NAME_GOODS 0.00234379          0
          4 NAME_CASH_ 0.00217685          0
          5 NAME_YIELD 0.00182527          0
          6 NAME_CONTR 0.00167882          0
          7 CHANNEL_TY 0.00159832          0
          8 NAME_TYPE_ 0.00157290          0
          9 DAYS_FIRST 0.00151427     0.6166
         10 NAME_SELLE 0.00148878          0
         11 CODE_REJEC 0.00146265          0
         12 RATE_DOWN_ 0.00084979     0.4952
         13 NAME_CONTR 0.00080413          0
         14 NAME_PAYME 0.00080269          0
        ...        ...        ...        ...

##  Information Gain and Frequency of Features in Previous Application
#### *Top 25 Features are-*
![DA](pre.png)

In [24]:
sql = <<SQL
create temp table installments_payments_temp
as select * from installments_payments as a join 
(select application_train.SK_ID_CURR, application_train.TARGET from application_train) b
on a.SK_ID_CURR == b.SK_ID_CURR
limit 10000
SQL

begin
db.execute(sql) 
rescue 
db.execute("drop table installments_payments_temp")
db.execute(sql)
end


table = get_info_gain db,"installments_payments_temp"
table = table.sort_by do |item|
   -item[1].to_f
end 
#puts table
column1 = table.collect {|x| x[0]}
column2 = table.collect {|x| x[1]}
column3 = table.collect {|x| x[3]}

df = Daru::DataFrame.new({"Feature Name" => column1, "Information Gain" => column2 , "Frequency" => column3})

#<Daru::DataFrame(9x3)>
            Feature Na Informatio  Frequency
          0     TARGET 0.39687166        1.0
          1 SK_ID_CURR 0.00040798        1.0
          2 DAYS_ENTRY 0.00040213        1.0
          3 DAYS_INSTA 0.00039248        1.0
          4 SK_ID_PREV 0.00037570        1.0
          5 NUM_INSTAL 0.00028352        1.0
          6 AMT_PAYMEN 0.00015343        1.0
          7 AMT_INSTAL 0.00012981        1.0
          8 NUM_INSTAL 9.43944928        1.0

##  Information Gain and Frequency of Features in Installments payments
#### *All Features are-*
![DA](ip.png)

In [25]:
sql = <<SQL
create temp table credit_card_balance_temp
as select * from credit_card_balance as a join 
(select application_train.SK_ID_CURR, application_train.TARGET from application_train) b
on a.SK_ID_CURR == b.SK_ID_CURR
limit 10000
SQL

begin
db.execute(sql) 
rescue 
db.execute("drop table credit_card_balance_temp")
db.execute(sql)
end


table = get_info_gain db,"credit_card_balance_temp"
table = table.sort_by do |item|
   -item[1].to_f
end 
#puts table
column1 = table.collect {|x| x[0]}
column2 = table.collect {|x| x[1]}
column3 = table.collect {|x| x[3]}

df = Daru::DataFrame.new({"Feature Name" => column1, "Information Gain" => column2 , "Frequency" => column3})

#<Daru::DataFrame(24x3)>
            Feature Na Informatio  Frequency
          0     TARGET 0.38503602        1.0
          1 AMT_BALANC 0.00318197        1.0
          2 AMT_RECIVA 0.00316970        1.0
          3 AMT_TOTAL_ 0.00316970        1.0
          4 AMT_RECEIV 0.00282521        1.0
          5 CNT_DRAWIN 0.00240306     0.8051
          6 AMT_INST_M 0.00233732     0.9623
          7 MONTHS_BAL 0.00143526        1.0
          8 CNT_DRAWIN 0.00091665        1.0
          9 CNT_DRAWIN 0.00065910     0.8051
         10 AMT_CREDIT 0.00053010        1.0
         11 AMT_DRAWIN 0.00049615     0.8051
         12 SK_ID_CURR 0.00037290        1.0
         13 CNT_INSTAL 0.00033138     0.9623
         14 AMT_DRAWIN 0.00029525        1.0
        ...        ...        ...        ...

##  Information Gain and Frequency of Features in Credit card balance
#### *All Features are-*
![DA](ccb.png)

In [3]:
x, y , a ,b = cod_ecdf db, "AMT_CREDIT"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe60e86a348 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe60e69d9e8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(166,206,227)"}, :data=>"6f8c3edc-e4d1-45e0-b877-15942dab003a"}, @xrange=[0.0, 1.0], @yrange=[0.00018221574344023323, 1.0]>, #<Nyaplot::Diagram:0x007fe60ea48660 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(31,120,180)"}, :data=>"60da890b-4b75-40c1-84a4-fd1e1d1f6714"}, @xrange=[0.0, 1.0], @yrange=[0.00039936102236421724, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.00018221574344023323, 1.0]}}>

## ECDF of AMT_CREDIT
![ecdf](./img/fig.png)

In [9]:
x, y , a ,b = cod_ecdf db, "DAYS_BIRTH"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007f98a648ddc0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f98a7111240 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(127,201,127)"}, :data=>"ae820d96-e4d5-4b49-aef5-e07b1afe7c6f"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>, #<Nyaplot::Diagram:0x007f98a5b372f8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(190,174,212)"}, :data=>"5fb3854b-9e20-4734-a864-0e224ccd3e73"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.0001, 1.0]}}>

## ECDF of DAYS_BIRTH
![ecdf](./img/fig-8.png)

In [6]:
x, y , a ,b = cod_ecdf db, "AMT_ANNUITY"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe6181504e0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe618217ea0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(127,201,127)"}, :data=>"b739ae31-ac10-4f6e-9fd3-e0e96526eee3"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>, #<Nyaplot::Diagram:0x007fe6181a22e0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(190,174,212)"}, :data=>"b596514b-b40d-4b40-a28f-173d3f04f5bb"}, @xrange=[0.0, 1.0], @yrange=[0.00016342539630658605, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.0001, 1.0]}}>

## ECDF of AMT_CREDIT
![ecdf](./img/fig-2.png)

In [7]:
x, y , a ,b = cod_ecdf db, "EXT_SOURCE_2"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe60e5577a0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe60e99b7f8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(166,206,227)"}, :data=>"6f2b1dba-f67f-4a0f-a067-f8a4f6d9e7f1"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>, #<Nyaplot::Diagram:0x007fe618203978 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(31,120,180)"}, :data=>"4b7fe810-6d86-45af-a3d4-6ebbec57aa2b"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.0001, 1.0]}}>

## ECDF of AMT_CREDIT
![ecdf](./img/fig-3.png)

In [8]:
x, y , a ,b = cod_ecdf db, "EXT_SOURCE_3"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe60e64cd68 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe618504870 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(102,194,165)"}, :data=>"c000183d-7811-4dfc-b7cc-4727df613afd"}, @xrange=[0.0, 1.0], @yrange=[0.0012642225031605564, 1.0]>, #<Nyaplot::Diagram:0x007fe61a8568a0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(252,141,98)"}, :data=>"6e05e1bd-821b-4b9e-a92e-647f37cbef14"}, @xrange=[0.0, 1.0], @yrange=[0.0013157894736842105, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.0012642225031605564, 1.0]}}>

## ECDF of AMT_CREDIT
![ecdf](./img/fig-4.png)

In [9]:
x, y , a ,b = cod_ecdf db, "EXT_SOURCE_1"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe6163aa6c0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe61609a660 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(127,201,127)"}, :data=>"a1ccfc6f-f1ab-47aa-a25a-a724af91beda"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>, #<Nyaplot::Diagram:0x007fe616288dc8 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(190,174,212)"}, :data=>"efc55faa-eb04-40d6-91cc-88d5edbdff55"}, @xrange=[0.0, 1.0], @yrange=[0.00010085728693898134, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.0001, 1.0]}}>

## ECDF of AMT_CREDIT
![ecdf](./img/fig-5.png)

In [11]:
x, y , a ,b = cod_ecdf db, "EXT_SOURCE_2/EXT_SOURCE_1"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe618516070 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe616907cd0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(141,211,199)"}, :data=>"c2cade1f-025c-4ac9-a5b3-975568538819"}, @xrange=[0.0, 1.0], @yrange=[0.00010001000100010001, 1.0]>, #<Nyaplot::Diagram:0x007fe614dfdbb0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(255,255,179)"}, :data=>"58c3a2c2-451c-4fe1-bb54-0bd3d37bc382"}, @xrange=[0.0, 1.0], @yrange=[0.00010001000100010001, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.00010001000100010001, 1.0]}}>

## ECDF of AMT_CREDIT
![ecdf](./img/fig-6.png)

In [12]:
x, y , a ,b = cod_ecdf db, "EXT_SOURCE_2*EXT_SOURCE_3"
df = Daru::DataFrame.new({
  x: x,
  y: y,
  c: ['Target 0']*a + ['Target 1']*b
  })

  df.to_category :c
  df[:c].type
  
  df.plot(type: :line, x: :x, y: :y, categorized: {by: :c, method: :color}) do |plot, diagram|
    plot.x_label "X"
    plot.y_label "Y"
  end

#<Nyaplot::Plot:0x007fe614c49e18 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe61496a148 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 0", :color=>"rgb(27,158,119)"}, :data=>"d9ca1fa5-243f-4cae-908d-a79d1eb6bba1"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>, #<Nyaplot::Diagram:0x007fe60e13ad48 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :title=>"Target 1", :color=>"rgb(217,95,2)"}, :data=>"5b6bf26a-bdea-4176-81f4-02a7fa9b6f67"}, @xrange=[0.0, 1.0], @yrange=[0.0001, 1.0]>], :options=>{:legend=>true, :x_label=>"X", :y_label=>"Y", :zoom=>true, :width=>800, :xrange=>[0.0, 1.0], :yrange=>[0.0001, 1.0]}}>

## ECDF of EXT_SOURCE_2*EXT_SOURCE_3
![ecdf](./img/fig-7.png)

In [7]:
cdata = db.execute("select TARGET, DAYS_BIRTH, DAYS_EMPLOYED from application_train limit 10000")
cdata = labelData cdata, column_types
k_means cdata, 5
x1 = []
x2 = []
  target = []
  cdata.each do |row|
    x1 << row["features"]["DAYS_BIRTH"]
    x2 << row["features"]["DAYS_EMPLOYED"]
    target << row["cluster"]
  end
  df = Daru::DataFrame.new({x1: x1, x2: x2, target: target})
  df.to_category :target
  df.plot(type: :scatter, x: :x1, y: :x2, categorized: {by: :target, method: :color}) do |plot, diagram|
    plot.x_label "DAYS_BIRTH"
    plot.y_label "DAYS_EMPLOYED"
    plot.legend false
  end

#<Nyaplot::Plot:0x007fe6e788d7d8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007fe6e7fb6b90 @properties={:type=>:scatter, :options=>{:x=>:x1, :y=>:x2, :title=>1, :color=>"rgb(228,26,28)", :tooltip_contents=>[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1